In [1]:
import pandas as pd
import numpy as np

In [74]:
df = pd.read_csv('../src/data/interactions.csv')
df_users = pd.read_csv('../src/data/users.csv')
df_items = pd.read_csv('../src/data/items.csv')

In [109]:
df_items.head()

id              title  \
0  128115   Ворон-челобитчик   
1  210979  Скрипка Ротшильда   
2   95632   Испорченные дети   
3  247906   Странный человек   
4  294280  Господа ташкентцы   

                                              genres                 authors  \
0  Зарубежные детские книги,Сказки,Зарубежная кла...  Михаил Салтыков-Щедрин   
1  Классическая проза,Литература 19 века,Русская ...             Антон Чехов   
2  Зарубежная классика,Классическая проза,Литерат...  Михаил Салтыков-Щедрин   
3             Пьесы и драматургия,Литература 19 века        Михаил Лермонтов   
4  Зарубежная классика,Классическая проза,Литерат...  Михаил Салтыков-Щедрин   

   year  
0  1886  
1  1894  
2  1869  
3  1831  
4  1873

In [3]:
df.head()

user_id  item_id  progress  rating  start_date
0   126706    14433        80     NaN  2018-01-01
1   127290   140952        58     NaN  2018-01-01
2    66991   198453        89     NaN  2018-01-01
3    46791    83486        23     5.0  2018-01-01
4    79313   188770        88     5.0  2018-01-01

In [4]:
df_users[df_users["user_id"] == 2].values.squeeze()

array([2, '18_24', 0.0], dtype=object)

In [5]:
df_users.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 142888 entries, 0 to 142887
Data columns (total 3 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   user_id  142888 non-null  int64  
 1   age      142742 non-null  object 
 2   sex      136626 non-null  float64
dtypes: float64(1), int64(1), object(1)
memory usage: 3.3+ MB


In [6]:
df_users.head()

user_id     age  sex
0        1   45_54  NaN
1        2   18_24  0.0
2        3  65_inf  0.0
3        4   18_24  0.0
4        5   35_44  0.0

In [7]:
df_items.head()

id              title  \
0  128115   Ворон-челобитчик   
1  210979  Скрипка Ротшильда   
2   95632   Испорченные дети   
3  247906   Странный человек   
4  294280  Господа ташкентцы   

                                              genres                 authors  \
0  Зарубежные детские книги,Сказки,Зарубежная кла...  Михаил Салтыков-Щедрин   
1  Классическая проза,Литература 19 века,Русская ...             Антон Чехов   
2  Зарубежная классика,Классическая проза,Литерат...  Михаил Салтыков-Щедрин   
3             Пьесы и драматургия,Литература 19 века        Михаил Лермонтов   
4  Зарубежная классика,Классическая проза,Литерат...  Михаил Салтыков-Щедрин   

   year  
0  1886  
1  1894  
2  1869  
3  1831  
4  1873

# Cold Start

## Возьмем самое популярное

In [7]:
items_name = df_items[['id', 'title']].set_index('id').sort_index()

In [8]:
items_count = pd.DataFrame(df[['item_id']].value_counts(), columns=['count']).sort_index()

In [9]:
count_titles = items_name.merge(items_count, left_index=True, right_on='item_id')

In [10]:
count_titles.sort_values(by='count', ascending=False).head(10)

title  count
item_id                                                          
99357    Сила подсознания, или Как изменить жизнь за 4 ...   6576
316995            Самая таинственная тайна и другие сюжеты   2706
109201                           Яблоки из сада Шлицбутера   2585
241026                                        Зелёная миля   2300
28889                         Сказки для идиотов (сборник)   2287
121687                                            Снеговик   2245
243711                                      Противостояние   2143
288531                                             Инферно   2138
90225                              Зулейха открывает глаза   2098
26963                                             Шантарам   2078

## Теперь попробуем почистить датасет

In [11]:
items_count = pd.DataFrame(df[df['progress'] > 40][['item_id']].value_counts(), columns=['count']).sort_index() 

In [12]:
count_titles = items_name.merge(items_count, left_index=True, right_on='item_id')

In [13]:
count_titles.sort_values(by='count', ascending=False).head(10)

title  count
item_id                                                          
90225                              Зулейха открывает глаза   1071
281005   Богатый папа, бедный папа. Роберт Кийосаки (об...    994
109201                           Яблоки из сада Шлицбутера    946
99357    Сила подсознания, или Как изменить жизнь за 4 ...    796
319390                                            Черновик    720
121687                                            Снеговик    699
264997                                               После    696
89152                                 50 правил умной дуры    595
159580                           Пятьдесят оттенков серого    542
112631                                         После ссоры    527

## Посмотрим какие жанры популярны

In [98]:
items_count = pd.DataFrame(df[df['progress'] > 40][['item_id']].value_counts(), columns=['count']).sort_index() 

In [99]:
items_name = df_items[['id', 'title', 'genres']].set_index('id').sort_index()

In [117]:
    items_count = pd.DataFrame(
            df[df["progress"] > 40][["item_id"]].value_counts(), columns=["count"]
    ).sort_index()
    items_name = df_items[['id', 'title', 'genres']].set_index('id').sort_index()
    items_name.genres = items_name.genres.fillna('Другие жанры')
    items_name.genres = items_name.genres.apply(lambda x: x.split(','))
    items_name_exlode = items_name.explode(column='genres')
    items_name_exlode = items_name_exlode[items_name_exlode['genres'] == 'Зарубежные приключения'][['title']]
    count_titles = items_name_exlode.merge(items_count, left_index=True, right_on='item_id')

count_titles.sort_values(by='count', ascending=False)['title'].values[:n]

array(['Шантарам', 'Тень горы', 'Таинственный остров', 'Повелитель мух',
       'Путешественник', 'Двадцать тысяч лье под водой',
       'Два года каникул', 'Песчаный дьявол', 'Женская война',
       'Граф Монте-Кристо', 'Плавающий город', 'Амазония',
       'Костяной лабиринт', 'Всадник без головы', 'Шестое вымирание',
       'Дети капитана Гранта', 'Седьмая казнь', 'Ледяные боги',
       'Крепкие мужчины', 'Пещера', 'Пять недель на воздушном шаре',
       'Мотылек', 'Айвенго', 'Приключения Тома Сойера', 'Сёгун',
       'Две Дианы', 'Белый клык', 'Сердца трех', 'Дети капитана Гранта',
       'Малыш', 'Тонкая работа', 'Первая ночь', 'Три мушкетера',
       'Дальнейшие приключения Робинзона Крузо', 'Черная Индия',
       'Королева Марго', 'Моби Дик, или Белый Кит', 'Песнь бича',
       'Графиня де Монсоро', 'Ким', 'Юные путешественники',
       'Королева Марго',
       'Ужас на поле для гольфа. Приключения Жюля де Грандена (сборник)',
       'Тайпан', 'Порочный круг', 'Айвенго', 'Влюбле

In [84]:
count_titles.genres = count_titles.genres.fillna('NaN')

In [85]:
count_titles.genres = count_titles.genres.apply(lambda x: x.split(','))

In [86]:
count_titles_exlode = count_titles.explode(column='genres') #.pivot_table(index='title', columns='genres')

In [92]:
count_titles_exlode[count_titles_exlode['genres'] == 'Зарубежные приключения'][['title', 'count']].sort_values(by='count', ascending=False)

title  count
item_id                                                          
26963                                             Шантарам    462
306416                                           Тень горы    136
292066                                 Таинственный остров    112
198593                                      Повелитель мух     86
108078                                      Путешественник     59
...                                                    ...    ...
284119                                     The Black Arrow      2
22209                         Приключения бригадира Жерара      2
170237   В сердце моря. Трагедия китобойного судна «Эсс...      2
29758                         Приключения в стране бизонов      1
193348                                      Люцифер. Том 2      1

[454 rows x 2 columns]

In [93]:
items_name

title  \
id                                                          
1                          Множественные источники дохода   
2       Она не объясняет, он не догадывается. Японское...   
13                                                Падение   
21                 Надо жить умеючи. Архетипы нового века   
26                       Сетевой маркетинг: методы продаж   
...                                                   ...   
321732                           Молитвы на разные случаи   
321733              Доктор Кто. Герои и монстры (сборник)   
321739                                  Человек в футляре   
321748                        Хочешь, я буду твоей мамой?   
321751                                        Сердца трех   

                                                   genres  
id                                                         
1       Эффективность бизнеса,Финансовый менеджмент,Пр...  
2       Семейная психология,Зарубежная психология,Соци...  
13      Зарубежные любовные романы,Остросюжетные любов...  
21      Прикладная литература,Общая психология,Публици...  
26      Рукоделие и ремесла,Просто о бизнесе,Другие сп...  
...                                                   ...  
321732                  Православные молитвы,Христианство  
321733  Боевая фантастика,Зарубежная фантастика,Космич...  
321739                     Современная русская литература  
321748                                   Воспитание детей  
321751        Книги о приключениях,Зарубежные приключения  

[59599 rows x 2 columns]

# Preproc

In [10]:
df_users.isna().sum()

user_id       0
age         146
sex        6262
dtype: int64

In [17]:
df_items.isna().sum()

id             0
title          0
genres        31
authors     6885
year       12879
dtype: int64

In [26]:
df_items['year'].mode()

0    2018
Name: year, dtype: object

In [85]:
def proc_users(df_users: pd.DataFrame):
    import pandas as pd

    # загрузка данных
    df_users = df_users.copy()

    # заполнение пропущенных значений возраста модой
    df_users['age'].fillna(df_users[df_users['age'].notna()]['age'].mode()[0], inplace=True)

    # заполнение пропущенных значений пола модой
    df_users['sex'].fillna(df_users[df_users['age'].notna()]['sex'].mode()[0], inplace=True)
    
    return df_users


def extract_year(text):
    import re
    pattern = r'\b\d{4}\b'
    match = re.search(pattern, text)
    if match:
        return int(match.group())
    else:
        return None


def proc_items(df_items: pd.DataFrame):
    import pandas as pd
    import datetime
    # загрузка данных
    df_items = df_items.copy()

    # заполнение пропущенных значений возраста модой
    df_items['genres'].fillna('Unknown', inplace=True)
    df_items['authors'].fillna('Unknown', inplace=True)
    
    df_items['year'] = df_items['year'].apply(lambda x: extract_year(str(x)))
    df_items.loc[df_items['year'].isna(), 'year'] = np.nan
    
    df_items['year'] = pd.to_numeric(df_items['year'], errors='coerce')
    df_items.loc[df_items['year'] > datetime.date.today().year, 'year'] = np.nan
    mean_year = df_items['year'].mean()
    df_items['year'].fillna(mean_year, inplace=True)
    
    return df_items


In [92]:
df.isna().sum()

user_id             0
item_id             0
progress            0
rating        1247722
start_date          0
dtype: int64

# Rec Sys

## ALS

KeyError: '[238391, 1090096, 1034115, 163732, 377269, 295173, 986364, 802912, 303043, 1087680, 280035, 911317, 259205, 729358, 268386, 901561, 278917, 224718, 487531, 386154, 834281, 266680, 238444, 793154, 538025, 1036444, 299277, 39016, 897092, 869584, 448208, 102545, 74963, 579972, 90491, 1011033, 460825, 799277, 912609, 101289, 345000, 457442, 35693, 485643, 613173, 461820, 46216, 522246, 876160, 831490, 680549, 194607, 287206, 289326, 87474, 617958, 78863, 91197, 872563, 794975, 817484, 103671, 517374, 59936, 130172, 111580, 125181, 54402, 590029, 49921, 1066301, 919469, 998118, 1043842, 1050109, 75881, 128528, 306026, 998756, 875878, 1090135, 5706, 19003, 340909, 191197, 139331, 1038805, 19101, 419658, 349089, 422793, 605930, 684104, 6314, 662635, 601044, 654835, 328583, 695903, 663138, 747357, 662391, 699865, 625335, 600350, 4554, 284654, 905309, 118440, 326331, 454256, 1032523, 908848, 420525, 97277, 790119, 553194, 714766, 556037, 547046, 779055, 427339, 403436, 288932, 569729

In [104]:
df

user_id  item_id  progress  rating  start_date
0         126706    14433        80     NaN  2018-01-01
1         127290   140952        58     NaN  2018-01-01
2          66991   198453        89     NaN  2018-01-01
3          46791    83486        23     5.0  2018-01-01
4          79313   188770        88     5.0  2018-01-01
...          ...      ...       ...     ...         ...
1533073    76968   285394        95     NaN  2019-12-31
1533074   153877   285394        76     5.0  2019-12-31
1533075    90021    73789        97     NaN  2019-12-31
1533076     6452    77993        39     NaN  2019-12-31
1533077    70445   230195         2     NaN  2019-12-31

[1533078 rows x 5 columns]